In [4]:
# Initialize an empty list to store rows
rows = []

# Open the file in read mode with UTF-8 encoding
with open(filename, "r", encoding="utf-8") as f:
    # Create a CSV reader object
    reader = csv.reader(f)
    # Read the header row and store it separately
    header = next(reader)
    # Iterate over each row in the file and append it to the rows list
    for row in reader:
        rows.append(row)

# Add a new header for the sentiment column
header.append("Sentiment")

In [5]:
print(header)

['id', 'u_id', 'u_description', 'u_name', 'u_screen_name', 'u_lang', 'u_statuses_count', 'u_followers_count', 'u_friends_count', 'latitude', 'longitude', 'type', 'place_type', 'area', 'c_country', 'c_state', 'c_county', 'c_geoid', 'created_at', 'hashtags', 'text', 'Sentiment']


In [6]:
# Loop over each row and perform sentiment analysis
for row in rows:
    # Extract the text to be analyzed from the Second column of the row
    text = row[-1]
    # Create a prompt for the sentiment analysis API with the text
    prompt = f"Please analyze the sentiment of the following text:{text}"
    # Call the sentiment analysis API with the prompt
    response = openai.Completion.create(
        engine="text-davinci-002",
        prompt=prompt,
        temperature=0,
        max_tokens=128,  # Increase max_tokens to retrieve more than one token
        n=1,
        stop=None,
        timeout=10,
    )
    # Extract the sentiment from the API response
    sentiment = response.choices[0].text.strip().replace("The sentiment of the text is ", "").rstrip('.')
    # Map the sentiment to a more concise label
    if "Positive" in sentiment:
        sentiment = "Positive"
    elif "Negative" in sentiment:
        sentiment = "Negative"
    elif "Neutral" in sentiment:
        sentiment = "Neutral"
    # Append the sentiment to the row
    row.append(sentiment)
    # Print the text and its corresponding sentiment
    print(f"{text} -> {sentiment}")
    # Pause for 0.5 seconds to avoid hitting API rate limits
    time.sleep(0.5)


RateLimitError: ignored

## distilbert-base-uncased

In [4]:
%pip install transformers torch

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.7/7.7 MB 30.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.0/302.0 kB 36.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 73.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 71.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 295.0/295.0 kB 35.9 MB/s eta 0:00:00


In [3]:
import pandas as pd

# Replace 'your_data.csv' with the actual file path
df = pd.read_csv('sample_data/jurong.csv')
sample_df= df.head(1000)

In [8]:
from transformers import DistilBertTokenizer, DistilBertForSequenceClassification
import torch

model_name = "distilbert-base-uncased"
model = DistilBertForSequenceClassification.from_pretrained(model_name)
tokenizer = DistilBertTokenizer.from_pretrained(model_name)


Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['pre_classifier.weight', 'classifier.bias', 'classifier.weight', 'pre_classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [9]:
sentiment_labels = []

for index, row in df.head(1000).iterrows():
    text = row['text']  # Replace 'text_column' with the name of the column containing the text
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=512)

    with torch.no_grad():
        outputs = model(**inputs)

    predicted_class = torch.argmax(outputs.logits)
    sentiment_label = predicted_class.item()
    sentiment_labels.append(sentiment_label)

sample_df = df.head(1000)
# Add the sentiment labels to the DataFrame
sample_df.loc[:999, 'sentiment'] = sentiment_labels

<ipython-input-9-1db0773e3647>:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sample_df.loc[:999, 'sentiment'] = sentiment_labels
<ipython-input-9-1db0773e3647>:16: DeprecationWarning: In a future version, `df.iloc[:, i] = newvals` will attempt to set the values inplace instead of always setting a new array. To retain the old behavior, use either `df[df.columns[i]] = newvals` or, if columns are non-unique, `df.isetitem(i, newvals)`
  sample_df.loc[:999, 'sentiment'] = sentiment_labels


In [10]:
sample_df

id        u_id  \
0    5.517160e+17  2524405117   
1    5.517180e+17   580964411   
2    5.517180e+17   362635979   
3    5.517140e+17   155105541   
4    5.517160e+17  1550806381   
..            ...         ...   
995  6.542890e+17  1010336558   
996  6.542940e+17   998601715   
997  6.545260e+17  2566181784   
998  6.545280e+17   941450437   
999  6.545130e+17   850508713   

                                         u_description      u_name  \
0                                                  Nwc   Jeannette   
1                                  ig: @/asmaanaabilah     nabilah   
2                         Just one shot is all i need.   ˙ɹɾ ʇɐɯɐɯ   
3                  Idle minds are the devil's workshop        Ryan   
4    because it's easier to get hated than loved. -...      ✽你的皇后✽   
..                                                 ...         ...   
995                               我爱你 @fxckattachments          Qi   
996                           I leave my life to fate.      shine.   
997                                       Life goes on        jon.   
998                                             +65 ♎️        ｌｏｓｔ   
999                Always laugh no matter what happens  Derrick Ng   

      u_screen_name u_lang  u_statuses_count  u_followers_count  \
0    twentyfifthxx_     en            8293.0              165.0   
1     AsmaaNaabilah     en           62376.0              907.0   
2        MatZhamJoe     en           19526.0              152.0   
3           d0urnut     en           13236.0              475.0   
4     KatherineLzt_     en           66416.0              679.0   
..              ...    ...               ...                ...   
995           lyqcx     en           16269.0              784.0   
996  shinegohfusong     en           12329.0              314.0   
997         JonC11_     en            2872.0              186.0   
998      yknowsebas     en           15426.0              275.0   
999        OkLahPRO     en           10155.0               99.0   

     u_friends_count  latitude  ...  place_type area c_country  c_state  \
0              399.0  1.339813  ...       admin  NaN       SGP      NaN   
1              761.0  1.345671  ...       admin  NaN       SGP      NaN   
2              145.0  1.311745  ...       admin  NaN       SGP      NaN   
3              400.0  1.352387  ...       admin  NaN       SGP      NaN   
4              564.0  1.334701  ...       admin  NaN       SGP      NaN   
..               ...       ...  ...         ...  ...       ...      ...   
995            306.0  1.315205  ...       admin  NaN       SGP      NaN   
996            295.0  1.344360  ...       admin  NaN       SGP      NaN   
997            182.0  1.347160  ...       admin  NaN       SGP      NaN   
998            173.0  1.352016  ...       admin  NaN       SGP      NaN   
999            126.0  1.344142  ...       admin  NaN       SGP      NaN   

    c_county  c_geoid      created_at  hashtags  \
0        NaN      NaN    4/1/15 07:23       NaN   
1        NaN      NaN    4/1/15 07:34       NaN   
2        NaN      NaN    4/1/15 07:34       NaN   
3        NaN      NaN    4/1/15 07:19       NaN   
4        NaN      NaN    4/1/15 07:26       NaN   
..       ...      ...             ...       ...   
995      NaN      NaN  14/10/15 09:32       NaN   
996      NaN      NaN  14/10/15 09:54       NaN   
997      NaN      NaN  15/10/15 01:13       NaN   
998      NaN      NaN  15/10/15 01:22       NaN   
999      NaN      NaN  15/10/15 00:22       NaN   

                                                  text sentiment  
0    I'm at Jurong Point in Singapore w/ @jxgssr_ h...         1  
1                                    sch tomorrow woop         1  
2                 Dinner w/ fam http://t.co/y5vlK7B7G7         1  
3    Please don't matter to me more than I matter t...         1  
4    “@ItsLifeFact: If you love someone, don't wait...         1  
..                                                 ...  

from matplotlib import pyplot as plt
_df_0['index'].plot(kind='hist', bins=20, title='index')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_1['id'].plot(kind='hist', bins=20, title='id')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_2['u_id'].plot(kind='hist', bins=20, title='u_id')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_3['u_statuses_count'].plot(kind='hist', bins=20, title='u_statuses_count')
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  from matplotlib import pyplot as plt
  import seaborn as sns
  palette = list(sns.palettes.mpl_palette('Dark2'))
  xs = series['index']
  ys = series['u_followers_count']
  
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_11.sort_values('index', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('index')
_ = plt.ylabel('u_followers_count')

from matplotlib import pyplot as plt
_df_12['index'].plot(kind='line', figsize=(8, 4), title='index')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_13['id'].plot(kind='line', figsize=(8, 4), title='id')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_14['u_id'].plot(kind='line', figsize=(8, 4), title='u_id')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_15['u_statuses_count'].plot(kind='line', figsize=(8, 4), title='u_statuses_count')
plt.gca().spines[['top', 'right']].set_visible(False)

## Twitter based Roberta

In [11]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer
import torch
import pandas as pd

# Load the pre-trained sentiment analysis model
model_name = "cardiffnlp/twitter-roberta-base-sentiment"
model = AutoModelForSequenceClassification.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)

# Load your DataFrame (replace 'your_data.csv' with your actual file path)

# Define a function to perform sentiment analysis and add labels to the DataFrame
def analyze_sentiment(text):
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=512)
    with torch.no_grad():
        outputs = model(**inputs)

    predicted_class = torch.argmax(outputs.logits)
    sentiment_label = model.config.id2label[predicted_class.item()]
    return sentiment_label

# Apply sentiment analysis to each row in the DataFrame
sample_df['sentiment_tweetroberta'] = sample_df['text'].apply(analyze_sentiment)

# Save the DataFrame with sentiment labels to a new CSV file
sample_df.to_csv('labeled_data.csv', index=False)

<ipython-input-11-39dc77000710>:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sample_df['sentiment_tweetroberta'] = sample_df['text'].apply(analyze_sentiment)


In [12]:
sample_df

id        u_id  \
0    5.517160e+17  2524405117   
1    5.517180e+17   580964411   
2    5.517180e+17   362635979   
3    5.517140e+17   155105541   
4    5.517160e+17  1550806381   
..            ...         ...   
995  6.542890e+17  1010336558   
996  6.542940e+17   998601715   
997  6.545260e+17  2566181784   
998  6.545280e+17   941450437   
999  6.545130e+17   850508713   

                                         u_description      u_name  \
0                                                  Nwc   Jeannette   
1                                  ig: @/asmaanaabilah     nabilah   
2                         Just one shot is all i need.   ˙ɹɾ ʇɐɯɐɯ   
3                  Idle minds are the devil's workshop        Ryan   
4    because it's easier to get hated than loved. -...      ✽你的皇后✽   
..                                                 ...         ...   
995                               我爱你 @fxckattachments          Qi   
996                           I leave my life to fate.      shine.   
997                                       Life goes on        jon.   
998                                             +65 ♎️        ｌｏｓｔ   
999                Always laugh no matter what happens  Derrick Ng   

      u_screen_name u_lang  u_statuses_count  u_followers_count  \
0    twentyfifthxx_     en            8293.0              165.0   
1     AsmaaNaabilah     en           62376.0              907.0   
2        MatZhamJoe     en           19526.0              152.0   
3           d0urnut     en           13236.0              475.0   
4     KatherineLzt_     en           66416.0              679.0   
..              ...    ...               ...                ...   
995           lyqcx     en           16269.0              784.0   
996  shinegohfusong     en           12329.0              314.0   
997         JonC11_     en            2872.0              186.0   
998      yknowsebas     en           15426.0              275.0   
999        OkLahPRO     en           10155.0               99.0   

     u_friends_count  latitude  ...  area c_country c_state  c_county c_geoid  \
0              399.0  1.339813  ...   NaN       SGP     NaN       NaN     NaN   
1              761.0  1.345671  ...   NaN       SGP     NaN       NaN     NaN   
2              145.0  1.311745  ...   NaN       SGP     NaN       NaN     NaN   
3              400.0  1.352387  ...   NaN       SGP     NaN       NaN     NaN   
4              564.0  1.334701  ...   NaN       SGP     NaN       NaN     NaN   
..               ...       ...  ...   ...       ...     ...       ...     ...   
995            306.0  1.315205  ...   NaN       SGP     NaN       NaN     NaN   
996            295.0  1.344360  ...   NaN       SGP     NaN       NaN     NaN   
997            182.0  1.347160  ...   NaN       SGP     NaN       NaN     NaN   
998            173.0  1.352016  ...   NaN       SGP     NaN       NaN     NaN   
999            126.0  1.344142  ...   NaN       SGP     NaN       NaN     NaN   

         created_at  hashtags  \
0      4/1/15 07:23       NaN   
1      4/1/15 07:34       NaN   
2      4/1/15 07:34       NaN   
3      4/1/15 07:19       NaN   
4      4/1/15 07:26       NaN   
..              ...       ...   
995  14/10/15 09:32       NaN   
996  14/10/15 09:54       NaN   
997  15/10/15 01:13       NaN   
998  15/10/15 01:22       NaN   
999  15/10/15 00:22       NaN   

                                                  text sentiment  \
0    I'm at Jurong Point in Singapore w/ @jxgssr_ h...         1   
1                                    sch tomorrow woop         1   
2                 Dinner w/ fam http://t.co/y5vlK7B7G7         1   
3    Please don't matter to me more than I matter t...         1   
4    “@ItsLifeFact: If you love someone, don't wait...         1   
..                                                 ...       ...   
995  I'm at Clementi MRT Station (EW23) - @smrt_sin...         1   
996  I'm at Lakeside MRT Station (EW26) - @smrt_sin...    

from matplotlib import pyplot as plt
_df_16['index'].plot(kind='hist', bins=20, title='index')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_17['id'].plot(kind='hist', bins=20, title='id')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_18['u_id'].plot(kind='hist', bins=20, title='u_id')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_19['u_statuses_count'].plot(kind='hist', bins=20, title='u_statuses_count')
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  from matplotlib import pyplot as plt
  import seaborn as sns
  palette = list(sns.palettes.mpl_palette('Dark2'))
  xs = series['index']
  ys = series['u_followers_count']
  
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_27.sort_values('index', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('index')
_ = plt.ylabel('u_followers_count')

from matplotlib import pyplot as plt
_df_28['index'].plot(kind='line', figsize=(8, 4), title='index')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_29['id'].plot(kind='line', figsize=(8, 4), title='id')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_30['u_id'].plot(kind='line', figsize=(8, 4), title='u_id')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_31['u_statuses_count'].plot(kind='line', figsize=(8, 4), title='u_statuses_count')
plt.gca().spines[['top', 'right']].set_visible(False)

##BertTweet

In [19]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer
import torch
import pandas as pd

# Load the pre-trained sentiment analysis model
model_name = "vinai/bertweet-base"
model = AutoModelForSequenceClassification.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)

# Load your DataFrame (replace 'your_data.csv' with your actual file path)

# Define a function to perform sentiment analysis and add labels to the DataFrame
def analyze_sentiment(text):
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=512)
    with torch.no_grad():
        outputs = model(**inputs)

    predicted_class = torch.argmax(outputs.logits)
    sentiment_label = model.config.id2label[predicted_class.item()]
    return sentiment_label

# Apply sentiment analysis to each row in the DataFrame
sample_df['bert_tweet'] = sample_df['text'].apply(analyze_sentiment)



Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at vinai/bertweet-base and are newly initialized: ['classifier.out_proj.weight', 'classifier.dense.bias', 'classifier.out_proj.bias', 'classifier.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
<ipython-input-19-bd2c303386d1>:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sample_df['bert_tweet'] = sample_df['text'].apply(analyze_sentiment)


In [17]:
%pip install emoji==0.6.0

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 51.0/51.0 kB 1.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for emoji: filename=emoji-0.6.0-py3-none-any.whl size=49721 sha256=f54f1655c92b7b3dca36d039899f71c5ca94c77bd5a65110be36a06bab71dce0
  Stored in directory: /root/.cache/pip/wheels/1b/bd/d9/310c33c45a553798a714e27e3b8395d37128425442b8c78e07
Successfully built emoji


In [20]:
sample_df

id        u_id  \
0    5.517160e+17  2524405117   
1    5.517180e+17   580964411   
2    5.517180e+17   362635979   
3    5.517140e+17   155105541   
4    5.517160e+17  1550806381   
..            ...         ...   
995  6.542890e+17  1010336558   
996  6.542940e+17   998601715   
997  6.545260e+17  2566181784   
998  6.545280e+17   941450437   
999  6.545130e+17   850508713   

                                         u_description      u_name  \
0                                                  Nwc   Jeannette   
1                                  ig: @/asmaanaabilah     nabilah   
2                         Just one shot is all i need.   ˙ɹɾ ʇɐɯɐɯ   
3                  Idle minds are the devil's workshop        Ryan   
4    because it's easier to get hated than loved. -...      ✽你的皇后✽   
..                                                 ...         ...   
995                               我爱你 @fxckattachments          Qi   
996                           I leave my life to fate.      shine.   
997                                       Life goes on        jon.   
998                                             +65 ♎️        ｌｏｓｔ   
999                Always laugh no matter what happens  Derrick Ng   

      u_screen_name u_lang  u_statuses_count  u_followers_count  \
0    twentyfifthxx_     en            8293.0              165.0   
1     AsmaaNaabilah     en           62376.0              907.0   
2        MatZhamJoe     en           19526.0              152.0   
3           d0urnut     en           13236.0              475.0   
4     KatherineLzt_     en           66416.0              679.0   
..              ...    ...               ...                ...   
995           lyqcx     en           16269.0              784.0   
996  shinegohfusong     en           12329.0              314.0   
997         JonC11_     en            2872.0              186.0   
998      yknowsebas     en           15426.0              275.0   
999        OkLahPRO     en           10155.0               99.0   

     u_friends_count  latitude  ...  c_country c_state c_county  c_geoid  \
0              399.0  1.339813  ...        SGP     NaN      NaN      NaN   
1              761.0  1.345671  ...        SGP     NaN      NaN      NaN   
2              145.0  1.311745  ...        SGP     NaN      NaN      NaN   
3              400.0  1.352387  ...        SGP     NaN      NaN      NaN   
4              564.0  1.334701  ...        SGP     NaN      NaN      NaN   
..               ...       ...  ...        ...     ...      ...      ...   
995            306.0  1.315205  ...        SGP     NaN      NaN      NaN   
996            295.0  1.344360  ...        SGP     NaN      NaN      NaN   
997            182.0  1.347160  ...        SGP     NaN      NaN      NaN   
998            173.0  1.352016  ...        SGP     NaN      NaN      NaN   
999            126.0  1.344142  ...        SGP     NaN      NaN      NaN   

         created_at  hashtags  \
0      4/1/15 07:23       NaN   
1      4/1/15 07:34       NaN   
2      4/1/15 07:34       NaN   
3      4/1/15 07:19       NaN   
4      4/1/15 07:26       NaN   
..              ...       ...   
995  14/10/15 09:32       NaN   
996  14/10/15 09:54       NaN   
997  15/10/15 01:13       NaN   
998  15/10/15 01:22       NaN   
999  15/10/15 00:22       NaN   

                                                  text  sentiment  \
0    I'm at Jurong Point in Singapore w/ @jxgssr_ h...          1   
1                                    sch tomorrow woop          1   
2                 Dinner w/ fam http://t.co/y5vlK7B7G7          1   
3    Please don't matter to me more than I matter t...          1   
4    “@ItsLifeFact: If you love someone, don't wait...          1   
..                                                 ...        ...   
995  I'm at Clementi MRT Station (EW23) - @smrt_sin...          1   
996  I'm at Lakeside MRT Station (EW26) - @smrt_sin...          1   
997  I'm at Fuhua Secondary School in Sin

from matplotlib import pyplot as plt
sample_df['id'].plot(kind='hist', bins=20, title='id')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
sample_df['u_id'].plot(kind='hist', bins=20, title='u_id')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
sample_df['u_statuses_count'].plot(kind='hist', bins=20, title='u_statuses_count')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
sample_df['u_followers_count'].plot(kind='hist', bins=20, title='u_followers_count')
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(sample_df['sentiment_tweetroberta'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(sample_df, x='id', y='sentiment_tweetroberta', inner='box', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(sample_df['bert_tweet'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(sample_df, x='id', y='bert_tweet', inner='box', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(sample_df['sentiment_tweetroberta'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(sample_df, x='u_id', y='sentiment_tweetroberta', inner='box', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(sample_df['bert_tweet'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(sample_df, x='u_id', y='bert_tweet', inner='box', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

Error: Runtime no longer has a reference to this dataframe, please re-run this cell and try again.


##TwHIN-BERT: A Socially-Enriched Pre-trained Language Model for Multilingual Tweet Representations

In [22]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer
import torch
import pandas as pd

# Load the pre-trained sentiment analysis model
model_name = "Twitter/twhin-bert-base"
model = AutoModelForSequenceClassification.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)

# Load your DataFrame (replace 'your_data.csv' with your actual file path)

# Define a function to perform sentiment analysis and add labels to the DataFrame
def analyze_sentiment(text):
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=512)
    with torch.no_grad():
        outputs = model(**inputs)

    predicted_class = torch.argmax(outputs.logits)
    sentiment_label = model.config.id2label[predicted_class.item()]
    return sentiment_label

# Apply sentiment analysis to each row in the DataFrame
sample_df['bert_twHin'] = sample_df['text'].apply(analyze_sentiment)

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at Twitter/twhin-bert-base and are newly initialized: ['classifier.bias', 'bert.pooler.dense.weight', 'classifier.weight', 'bert.pooler.dense.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
<ipython-input-22-4b2bfae2b2c9>:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sample_df['bert_twHin'] = sample_df['text'].apply(analyze_sentiment)


In [23]:
sample_df

id        u_id  \
0    5.517160e+17  2524405117   
1    5.517180e+17   580964411   
2    5.517180e+17   362635979   
3    5.517140e+17   155105541   
4    5.517160e+17  1550806381   
..            ...         ...   
995  6.542890e+17  1010336558   
996  6.542940e+17   998601715   
997  6.545260e+17  2566181784   
998  6.545280e+17   941450437   
999  6.545130e+17   850508713   

                                         u_description      u_name  \
0                                                  Nwc   Jeannette   
1                                  ig: @/asmaanaabilah     nabilah   
2                         Just one shot is all i need.   ˙ɹɾ ʇɐɯɐɯ   
3                  Idle minds are the devil's workshop        Ryan   
4    because it's easier to get hated than loved. -...      ✽你的皇后✽   
..                                                 ...         ...   
995                               我爱你 @fxckattachments          Qi   
996                           I leave my life to fate.      shine.   
997                                       Life goes on        jon.   
998                                             +65 ♎️        ｌｏｓｔ   
999                Always laugh no matter what happens  Derrick Ng   

      u_screen_name u_lang  u_statuses_count  u_followers_count  \
0    twentyfifthxx_     en            8293.0              165.0   
1     AsmaaNaabilah     en           62376.0              907.0   
2        MatZhamJoe     en           19526.0              152.0   
3           d0urnut     en           13236.0              475.0   
4     KatherineLzt_     en           66416.0              679.0   
..              ...    ...               ...                ...   
995           lyqcx     en           16269.0              784.0   
996  shinegohfusong     en           12329.0              314.0   
997         JonC11_     en            2872.0              186.0   
998      yknowsebas     en           15426.0              275.0   
999        OkLahPRO     en           10155.0               99.0   

     u_friends_count  latitude  ...  c_state c_county c_geoid      created_at  \
0              399.0  1.339813  ...      NaN      NaN     NaN    4/1/15 07:23   
1              761.0  1.345671  ...      NaN      NaN     NaN    4/1/15 07:34   
2              145.0  1.311745  ...      NaN      NaN     NaN    4/1/15 07:34   
3              400.0  1.352387  ...      NaN      NaN     NaN    4/1/15 07:19   
4              564.0  1.334701  ...      NaN      NaN     NaN    4/1/15 07:26   
..               ...       ...  ...      ...      ...     ...             ...   
995            306.0  1.315205  ...      NaN      NaN     NaN  14/10/15 09:32   
996            295.0  1.344360  ...      NaN      NaN     NaN  14/10/15 09:54   
997            182.0  1.347160  ...      NaN      NaN     NaN  15/10/15 01:13   
998            173.0  1.352016  ...      NaN      NaN     NaN  15/10/15 01:22   
999            126.0  1.344142  ...      NaN      NaN     NaN  15/10/15 00:22   

    hashtags                                               text  sentiment  \
0        NaN  I'm at Jurong Point in Singapore w/ @jxgssr_ h...          1   
1        NaN                                  sch tomorrow woop          1   
2        NaN               Dinner w/ fam http://t.co/y5vlK7B7G7          1   
3        NaN  Please don't matter to me more than I matter t...          1   
4        NaN  “@ItsLifeFact: If you love someone, don't wait...          1   
..       ...                                                ...        ...   
995      NaN  I'm at Clementi MRT Station (EW23) - @smrt_sin...          1   
996      NaN  I'm at Lakeside MRT Station (EW26) - @smrt_sin...          1   
997      NaN  I'm at Fuhua Secondary School in Singapore htt...          1   
998      NaN  You better OBEY BEY BEY BEY BEY @ Bukit Batok ...          1   
999      NaN                            @DancingSheeep I FAILED          1   

     sentiment_tweetroberta bert_tweet bert_twHin  
0         

from matplotlib import pyplot as plt
sample_df['id'].plot(kind='hist', bins=20, title='id')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
sample_df['u_id'].plot(kind='hist', bins=20, title='u_id')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
sample_df['u_statuses_count'].plot(kind='hist', bins=20, title='u_statuses_count')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
sample_df['u_followers_count'].plot(kind='hist', bins=20, title='u_followers_count')
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
import pandas as pd
plt.subplots(figsize=(8, 8))
df_2dhist = pd.DataFrame({
    x_label: grp['bert_twHin'].value_counts()
    for x_label, grp in sample_df.groupby('bert_tweet')
})
sns.heatmap(df_2dhist, cmap='viridis')
plt.xlabel('bert_tweet')
_ = plt.ylabel('bert_twHin')

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(sample_df['sentiment_tweetroberta'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(sample_df, x='id', y='sentiment_tweetroberta', inner='box', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(sample_df['bert_tweet'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(sample_df, x='id', y='bert_tweet', inner='box', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(sample_df['bert_twHin'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(sample_df, x='id', y='bert_twHin', inner='box', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(sample_df['sentiment_tweetroberta'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(sample_df, x='u_id', y='sentiment_tweetroberta', inner='box', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

## twitter-XLM-roBERTa-base for Sentiment Analysis



In [26]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer
import torch
import pandas as pd

# Load the pre-trained sentiment analysis model
MODEL = f"cardiffnlp/twitter-xlm-roberta-base-sentiment"

tokenizer = AutoTokenizer.from_pretrained(MODEL)
config = AutoConfig.from_pretrained(MODEL)

# PT
model = AutoModelForSequenceClassification.from_pretrained(MODEL)
model.save_pretrained(MODEL)

# Load your DataFrame (replace 'your_data.csv' with your actual file path)

# Define a function to perform sentiment analysis and add labels to the DataFrame
def analyze_sentiment(text):
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=512)
    with torch.no_grad():
        outputs = model(**inputs)

    predicted_class = torch.argmax(outputs.logits)
    sentiment_label = model.config.id2label[predicted_class.item()]
    return sentiment_label

# Apply sentiment analysis to each row in the DataFrame
sample_df['bert_tweet'] = sample_df['text'].apply(analyze_sentiment)

ValueError: ignored

##Pysentimento

In [30]:
%pip install pysentimiento

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 251.2/251.2 kB 6.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 493.7/493.7 kB 10.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 175.4/175.4 kB 11.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 14.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 16.8 MB/s eta 0:00:00
  Created wheel for emoji: filename=emoji-1.7.0-py3-none-any.whl size=171033 sha256=3a6ebf9121635039e940f8e27d00306c4d765b81e57132e3e5af042641d2b22e
  Stored in directory: /root/.cache/pip/wheels/31/8a/8c/315c9e5d7773f74b33d5ed33f075b49c6eaeb7cedbb86e2cf8
Successfully built emoji
  Attempting uninstall: emoji
    Found existing installation: emoji 0.6.0
    Uninstalling emoji-0.6.0:
      Successfully uninstalled emoji-0.6.0


In [34]:
%pip install accelerate -U

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 261.0/261.0 kB 4.5 MB/s eta 0:00:00
  Attempting uninstall: accelerate
    Found existing installation: accelerate 0.22.0
    Uninstalling accelerate-0.22.0:
      Successfully uninstalled accelerate-0.22.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
pysentimiento 0.7.2 requires accelerate<0.23.0,>=0.22.0, but you have accelerate 0.24.0 which is incompatible.


In [1]:
pip install transformers[torch]

In [5]:
import pandas as pd
from pysentimiento import create_analyzer
from pysentimiento.preprocessing import preprocess_tweet

# Load your DataFrame (replace 'your_data.csv' with your actual file path)
# Assuming you have a DataFrame named 'sample_df' with a 'text' column containing tweets.

# Initialize the SentimentAnalyzer
sentiment_analyzer = create_analyzer(task="sentiment", lang="en")

# Define a function to perform sentiment analysis and add labels to the DataFrame
def analyze_sentiment(text):
    result = sentiment_analyzer.predict(preprocess_tweet(text))
    return result

# Apply sentiment analysis to each row in the DataFrame
sample_df['sentiment_pysentimiento'] = sample_df['text'].apply(analyze_sentiment)

# Save the DataFrame with sentiment labels to a new CSV file
sample_df.to_csv('labeled_data_pysentimiento.csv', index=False)


<ipython-input-5-14d9a6b16c41>:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sample_df['sentiment_pysentimiento'] = sample_df['text'].apply(analyze_sentiment)


In [8]:
sample_df

id        u_id  \
0    5.517160e+17  2524405117   
1    5.517180e+17   580964411   
2    5.517180e+17   362635979   
3    5.517140e+17   155105541   
4    5.517160e+17  1550806381   
..            ...         ...   
995  6.542890e+17  1010336558   
996  6.542940e+17   998601715   
997  6.545260e+17  2566181784   
998  6.545280e+17   941450437   
999  6.545130e+17   850508713   

                                         u_description      u_name  \
0                                                  Nwc   Jeannette   
1                                  ig: @/asmaanaabilah     nabilah   
2                         Just one shot is all i need.   ˙ɹɾ ʇɐɯɐɯ   
3                  Idle minds are the devil's workshop        Ryan   
4    because it's easier to get hated than loved. -...      ✽你的皇后✽   
..                                                 ...         ...   
995                               我爱你 @fxckattachments          Qi   
996                           I leave my life to fate.      shine.   
997                                       Life goes on        jon.   
998                                             +65 ♎️        ｌｏｓｔ   
999                Always laugh no matter what happens  Derrick Ng   

      u_screen_name u_lang  u_statuses_count  u_followers_count  \
0    twentyfifthxx_     en              8293                165   
1     AsmaaNaabilah     en             62376                907   
2        MatZhamJoe     en             19526                152   
3           d0urnut     en             13236                475   
4     KatherineLzt_     en             66416                679   
..              ...    ...               ...                ...   
995           lyqcx     en             16269                784   
996  shinegohfusong     en             12329                314   
997         JonC11_     en              2872                186   
998      yknowsebas     en             15426                275   
999        OkLahPRO     en             10155                 99   

     u_friends_count  latitude  ...  place_type area c_country  c_state  \
0                399  1.339813  ...       admin  NaN       SGP      NaN   
1                761  1.345671  ...       admin  NaN       SGP      NaN   
2                145  1.311745  ...       admin  NaN       SGP      NaN   
3                400  1.352387  ...       admin  NaN       SGP      NaN   
4                564  1.334701  ...       admin  NaN       SGP      NaN   
..               ...       ...  ...         ...  ...       ...      ...   
995              306  1.315205  ...       admin  NaN       SGP      NaN   
996              295  1.344360  ...       admin  NaN       SGP      NaN   
997              182  1.347160  ...       admin  NaN       SGP      NaN   
998              173  1.352016  ...       admin  NaN       SGP      NaN   
999              126  1.344142  ...       admin  NaN       SGP      NaN   

    c_county  c_geoid      created_at  hashtags  \
0        NaN      NaN    4/1/15 07:23       NaN   
1        NaN      NaN    4/1/15 07:34       NaN   
2        NaN      NaN    4/1/15 07:34       NaN   
3        NaN      NaN    4/1/15 07:19       NaN   
4        NaN      NaN    4/1/15 07:26       NaN   
..       ...      ...             ...       ...   
995      NaN      NaN  14/10/15 09:32       NaN   
996      NaN      NaN  14/10/15 09:54       NaN   
997      NaN      NaN  15/10/15 01:13       NaN   
998      NaN      NaN  15/10/15 01:22       NaN   
999      NaN      NaN  15/10/15 00:22       NaN   

                                                  text  \
0    I'm at Jurong Point in Singapore w/ @jxgssr_ h...   
1                                    sch tomorrow woop   
2                 Dinner w/ fam http://t.co/y5vlK7B7G7   
3    Please don't matter to me more than I matter t...   
4    “@ItsLifeFact: If you love someone, don't wait...   
..                                                 ...   
995  I'm at Clementi MRT Station (EW23) - @smrt_sin.

##Bert

In [14]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer
import torch
import pandas as pd

# Load the pre-trained sentiment analysis model
model_name = "bert-base-uncased"
model = AutoModelForSequenceClassification.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)

# Load your DataFrame (replace 'your_data.csv' with your actual file path)

# Define a function to perform sentiment analysis and add labels to the DataFrame
def analyze_sentiment(text):
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=512)
    with torch.no_grad():
        outputs = model(**inputs)

    predicted_class = torch.argmax(outputs.logits)
    sentiment_label = model.config.id2label[predicted_class.item()]
    return sentiment_label

# Apply sentiment analysis to each row in the DataFrame
sample_df['bert_twHin'] = sample_df['text'].apply(analyze_sentiment)

<ipython-input-14-deb068d286f5>:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sample_df['bert_twHin'] = sample_df['text'].apply(analyze_sentiment)


In [15]:
sample_df

id        u_id  \
0    5.517160e+17  2524405117   
1    5.517180e+17   580964411   
2    5.517180e+17   362635979   
3    5.517140e+17   155105541   
4    5.517160e+17  1550806381   
..            ...         ...   
995  6.542890e+17  1010336558   
996  6.542940e+17   998601715   
997  6.545260e+17  2566181784   
998  6.545280e+17   941450437   
999  6.545130e+17   850508713   

                                         u_description      u_name  \
0                                                  Nwc   Jeannette   
1                                  ig: @/asmaanaabilah     nabilah   
2                         Just one shot is all i need.   ˙ɹɾ ʇɐɯɐɯ   
3                  Idle minds are the devil's workshop        Ryan   
4    because it's easier to get hated than loved. -...      ✽你的皇后✽   
..                                                 ...         ...   
995                               我爱你 @fxckattachments          Qi   
996                           I leave my life to fate.      shine.   
997                                       Life goes on        jon.   
998                                             +65 ♎️        ｌｏｓｔ   
999                Always laugh no matter what happens  Derrick Ng   

      u_screen_name u_lang  u_statuses_count  u_followers_count  \
0    twentyfifthxx_     en              8293                165   
1     AsmaaNaabilah     en             62376                907   
2        MatZhamJoe     en             19526                152   
3           d0urnut     en             13236                475   
4     KatherineLzt_     en             66416                679   
..              ...    ...               ...                ...   
995           lyqcx     en             16269                784   
996  shinegohfusong     en             12329                314   
997         JonC11_     en              2872                186   
998      yknowsebas     en             15426                275   
999        OkLahPRO     en             10155                 99   

     u_friends_count  latitude  ...  area c_country c_state  c_county c_geoid  \
0                399  1.339813  ...   NaN       SGP     NaN       NaN     NaN   
1                761  1.345671  ...   NaN       SGP     NaN       NaN     NaN   
2                145  1.311745  ...   NaN       SGP     NaN       NaN     NaN   
3                400  1.352387  ...   NaN       SGP     NaN       NaN     NaN   
4                564  1.334701  ...   NaN       SGP     NaN       NaN     NaN   
..               ...       ...  ...   ...       ...     ...       ...     ...   
995              306  1.315205  ...   NaN       SGP     NaN       NaN     NaN   
996              295  1.344360  ...   NaN       SGP     NaN       NaN     NaN   
997              182  1.347160  ...   NaN       SGP     NaN       NaN     NaN   
998              173  1.352016  ...   NaN       SGP     NaN       NaN     NaN   
999              126  1.344142  ...   NaN       SGP     NaN       NaN     NaN   

         created_at  hashtags  \
0      4/1/15 07:23       NaN   
1      4/1/15 07:34       NaN   
2      4/1/15 07:34       NaN   
3      4/1/15 07:19       NaN   
4      4/1/15 07:26       NaN   
..              ...       ...   
995  14/10/15 09:32       NaN   
996  14/10/15 09:54       NaN   
997  15/10/15 01:13       NaN   
998  15/10/15 01:22       NaN   
999  15/10/15 00:22       NaN   

                                                  text  \
0    I'm at Jurong Point in Singapore w/ @jxgssr_ h...   
1                                    sch tomorrow woop   
2                 Dinner w/ fam http://t.co/y5vlK7B7G7   
3    Please don't matter to me more than I matter t...   
4    “@ItsLifeFact: If you love someone, don't wait...   
..                                                 ...   
995  I'm at Clementi MRT Station (EW23) - @smrt_sin...   
996  I'm at Lakeside MRT Station (EW26) - @smrt_sin...   
997  I'm at Fuhua Secondary School in Singapore htt...   
998  You better OBEY B

from matplotlib import pyplot as plt
sample_df['id'].plot(kind='hist', bins=20, title='id')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
sample_df['u_id'].plot(kind='hist', bins=20, title='u_id')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
sample_df['u_statuses_count'].plot(kind='hist', bins=20, title='u_statuses_count')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
sample_df['u_followers_count'].plot(kind='hist', bins=20, title='u_followers_count')
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
sample_df['u_followers_count'].plot(kind='line', figsize=(8, 4), title='u_followers_count')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(sample_df['bert_twHin'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(sample_df, x='id', y='bert_twHin', inner='box', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(sample_df['bert_twHin'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(sample_df, x='u_id', y='bert_twHin', inner='box', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(sample_df['bert_twHin'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(sample_df, x='u_statuses_count', y='bert_twHin', inner='box', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(sample_df['bert_twHin'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(sample_df, x='u_followers_count', y='bert_twHin', inner='box', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

## K means clustering

In [10]:
import nltk
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to /root/nltk_data...


True

In [13]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.cluster import KMeans
from nltk.corpus import wordnet
from nltk.stem import WordNetLemmatizer

# Load your DataFrame (replace 'your_data.csv' with your actual file path)
# Assuming you have a DataFrame named 'tweets_df' with a 'text' column containing tweets.

# Define the number of clusters (k) you want to create
k = 10  # Adjust as needed

# Initialize the WordNet Lemmatizer
lemmatizer = WordNetLemmatizer()

# Tokenize and lemmatize the text data
def lemmatize_text(text):
    tokens = text.split()
    lemmatized_tokens = [lemmatizer.lemmatize(token, wordnet.VERB) for token in tokens]  # Lemmatize as verbs
    return ' '.join(lemmatized_tokens)

df['lemmatized_text'] = df['text'].apply(lemmatize_text)

# Initialize the TF-IDF vectorizer
tfidf_vectorizer = TfidfVectorizer(max_features=500)  # You can adjust the number of features as needed

# Fit and transform the lemmatized text data into TF-IDF vectors
tfidf_matrix = tfidf_vectorizer.fit_transform(df['lemmatized_text'])

# Initialize the K-means clustering model
kmeans = KMeans(n_clusters=k, random_state=0)

# Fit the model to the TF-IDF vectors
kmeans.fit(tfidf_matrix)

# Add cluster labels to the DataFrame
df['cluster_label'] = kmeans.labels_


/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


In [16]:
df.head(100)

id        u_id  \
0   5.517160e+17  2524405117   
1   5.517180e+17   580964411   
2   5.517180e+17   362635979   
3   5.517140e+17   155105541   
4   5.517160e+17  1550806381   
..           ...         ...   
95  5.517240e+17   306084657   
96  5.517250e+17   323743468   
97  5.517700e+17  2954976068   
98  5.517730e+17  1550806381   
99  5.517780e+17  1550806381   

                                        u_description           u_name  \
0                                                 Nwc        Jeannette   
1                                 ig: @/asmaanaabilah          nabilah   
2                        Just one shot is all i need.        ˙ɹɾ ʇɐɯɐɯ   
3                 Idle minds are the devil's workshop             Ryan   
4   because it's easier to get hated than loved. -...           ✽你的皇后✽   
..                                                ...              ...   
95              Hold my hand and bring me on picnics~  Little Mario :B   
96                  All i ever wanted was to be happy                B   
97                                    nayaliaa rizerr  nayalia rizeerr   
98  because it's easier to get hated than loved. -...           ✽你的皇后✽   
99  because it's easier to get hated than loved. -...           ✽你的皇后✽   

     u_screen_name u_lang  u_statuses_count  u_followers_count  \
0   twentyfifthxx_     en              8293                165   
1    AsmaaNaabilah     en             62376                907   
2       MatZhamJoe     en             19526                152   
3          d0urnut     en             13236                475   
4    KatherineLzt_     en             66416                679   
..             ...    ...               ...                ...   
95   SheCriedWolfe     en             70473                899   
96      BrendonABL     en              5266                145   
97       GirlsKpip     id                64                 22   
98   KatherineLzt_     en             66489                678   
99   KatherineLzt_     en             66526                679   

    u_friends_count  latitude  ...  area c_country c_state  c_county c_geoid  \
0               399  1.339813  ...   NaN       SGP     NaN       NaN     NaN   
1               761  1.345671  ...   NaN       SGP     NaN       NaN     NaN   
2               145  1.311745  ...   NaN       SGP     NaN       NaN     NaN   
3               400  1.352387  ...   NaN       SGP     NaN       NaN     NaN   
4               564  1.334701  ...   NaN       SGP     NaN       NaN     NaN   
..              ...       ...  ...   ...       ...     ...       ...     ...   
95             1117  1.323603  ...   NaN       SGP     NaN       NaN     NaN   
96              135  1.329521  ...   NaN       SGP     NaN       NaN     NaN   
97              109  1.349892  ...   NaN       SGP     NaN       NaN     NaN   
98              564  1.334791  ...   NaN       SGP     NaN       NaN     NaN   
99              564  1.334760  ...   NaN       SGP     NaN       NaN     NaN   

      created_at  hashtags                                               text  \
0   4/1/15 07:23       NaN  I'm at Jurong Point in Singapore w/ @jxgssr_ h...   
1   4/1/15 07:34       NaN                                  sch tomorrow woop   
2   4/1/15 07:34       NaN               Dinner w/ fam http://t.co/y5vlK7B7G7   
3   4/1/15 07:19       NaN  Please don't matter to me more than I matter t...   
4   4/1/15 07:26       NaN  “@ItsLifeFact: If you love someone, don't wait...   
..           ...       ...                                                ...   
95  4/1/15 07:58       NaN                             Just 3wks~ 😌 tahan je~   
96  4/1/15 08:02       NaN              @JiaChengNg @gomezenthusiast Fuck off   
97  4/1/15 11:01       NaN                                @hasanah_stevan hai   
98  4/1/15 11:12       NaN  Can u all calm down because honestly I'm nt ev...   
99  4/1/15 11:31       NaN                        Do u really understand me .   

             

from matplotlib import pyplot as plt
_df_0['id'].plot(kind='hist', bins=20, title='id')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_1['u_id'].plot(kind='hist', bins=20, title='u_id')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_2['u_statuses_count'].plot(kind='hist', bins=20, title='u_statuses_count')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_3['u_followers_count'].plot(kind='hist', bins=20, title='u_followers_count')
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
import pandas as pd
plt.subplots(figsize=(8, 8))
df_2dhist = pd.DataFrame({
    x_label: grp['hashtags'].value_counts()
    for x_label, grp in _df_14.groupby('u_lang')
})
sns.heatmap(df_2dhist, cmap='viridis')
plt.xlabel('u_lang')
_ = plt.ylabel('hashtags')

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_15['u_lang'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_15, x='id', y='u_lang', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_16['hashtags'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_16, x='id', y='hashtags', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_17['u_lang'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_17, x='u_id', y='u_lang', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_18['hashtags'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_18, x='u_id', y='hashtags', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

## Word net

In [19]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [20]:
import pandas as pd
from nltk.corpus import wordnet
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize

# Preprocessing and lemmatization
lemmatizer = WordNetLemmatizer()

def preprocess_and_lemmatize(text):
    words = word_tokenize(text)
    lemmatized_words = [lemmatizer.lemmatize(word) for word in words]
    return lemmatized_words

# Keywords related to a specific topic
topic_keywords = ["outdoor", "green", "sports", "pray"]

# Initialize an empty set to store keywords
keyword_set = set()

# Iterate through the 'text' column of the DataFrame to extract keywords
for tweet in df['text']:
    lemmatized_tweet = preprocess_and_lemmatize(tweet)
    for keyword in topic_keywords:
        if keyword in lemmatized_tweet:
            keyword_set.add(keyword)

# Convert the set of keywords to a list (if needed)
keyword_list = list(keyword_set)

# Print the extracted keywords
print("Keywords extracted from tweets:", keyword_list)


Keywords extracted from tweets: ['green', 'outdoor', 'pray']


In [21]:
import pandas as pd
from nltk.corpus import wordnet
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize

# Preprocessing and lemmatization
lemmatizer = WordNetLemmatizer()

def preprocess_and_lemmatize(text):
    words = word_tokenize(text)
    lemmatized_words = [lemmatizer.lemmatize(word) for word in words]
    return lemmatized_words

# Load your tweets from a pandas DataFrame (replace 'your_data.csv' with your actual file path)
# Assuming you have a DataFrame named 'tweets_df' with a 'text' column containing tweets.

# Initialize an empty set to store keywords
keyword_set = set()

# Iterate through the 'text' column of the DataFrame to extract keywords
for tweet in df['text']:
    lemmatized_tweet = preprocess_and_lemmatize(tweet)
    for word in lemmatized_tweet:
        # Check if the word is in WordNet (English)
        if wordnet.synsets(word):
            keyword_set.add(word)

# Convert the set of keywords to a list
keyword_list = list(keyword_set)

# Print the extracted keywords
print("Keywords extracted from tweets:", keyword_list)


Keywords extracted from tweets: ['quarrelling', 'LANGUAGE', 'REUNITE', 'romeo', 'TWO', 'Jordan', 'loading', 'parking', 'bioscience', 'HF', 'ga', 'copyright', 'fantasize', 'ACKNOWLEdgED', 'Checked', 'ROWS', 'fop', 'Cover', 'battleship', 'GOAT', 'sob', 'Struggling', 'innocently', 'reevaluate', 'Stella', 'cream', 'Bothered', 'anagram', 'Ate', 'ICECREAM', 'ISM', 'GRADE', 'Nagoya', 'Doe', 'Generally', 'thinner', 'Sour', 'cola', 'gearing', 'new', 'stirred', 'catch', 'secular', 'AWAKEN', 'SKIN', 'cocoa', 'MARCH', 'ACNE', 'Vendetta', 'IAs', 'hellish', 'DARE', 'ION', 'say', 'rendition', 'guess', 'Altitude', 'Broncho', 'offering', 'cAME', 'FANS', 'Wondering', 'LS', 'swinging', 'SCREwed', 'torch', 'Countrified', 'sagittarius', 'positive', 'energised', 'reign', 'Paras', 'decal', 'Oracle', 'followed', 'mute', 'mellows', 'hairy', 'Fall', 'PUSSY', 'Shitss', 'countdown', 'crib', 'bucket', 'foliage', 'wonky', 'fond', 'HOTEL', 'tarantula', 'hanging', 'ne', 'Saved', 'russian', 'myriad', 'Ws', 'Abundant',